In [1]:
import random
import time
# Two classes --> Player, Environment
# Player --> action(), totalReward,
# Environment --> displayBorad after action, curr_state, totalReward, each step reward,

#action (left, right, up, down)
class Player:
    def __init__(self):
        self.curr_state=0
        self.totalRewardReceived=0
        self.R = [-0.1,-0.1,-0.1,-0.1,1,-10,1,-0.1,10]
        
        self.Q = [[0,0,0,0],
                  [0,0,0,0],
                  [0,0,0,0],
                  [0,0,0,0],
                  [0,0,0,0],
                  [0,0,0,0],
                  [0,0,0,0],
                  [0,0,0,0],
                  [0,0,0,0]]
        
        self.Matrix = [
            [2,1,6,3],
            [0,2,7,4],
            [1,0,8,5],
            [5,4,0,6],
            [3,5,1,7],
            [4,3,2,8],
            [8,7,3,0],
            [6,8,4,1],
            [7,6,5,2]
        ]

        #N(s,a)
        self.count_of_states = [[0,0,0,0],
                               [0,0,0,0],
                               [0,0,0,0],
                               [0,0,0,0],
                               [0,0,0,0],
                               [0,0,0,0],
                               [0,0,0,0],
                               [0,0,0,0],
                               [0,0,0,0]]
        
        self.alpha = 0.1
        self.no_of_episodes = 0
        self.epsilon = 1
        self.gamma = 1
        
    def RL_Agent(self):
        # maintain visited states, rewards.
        # exploit using greedy policy with prob=0.4.
        # explore all possibility with prob=0.6/m.
        
        do = random.choices(["exploit", "explore"],weights=[1-self.epsilon, self.epsilon])[0]
        print(do)
        if (do=="exploit"):
            actions_with_max_Q_value = []
            max_Q_value = max(self.Q[self.curr_state])
            for i in range(4):
                if (self.Q[self.curr_state][i]==max_Q_value):
                    actions_with_max_Q_value.append(i)
            action = random.choice(actions_with_max_Q_value)
        else: # do == "explore"
            action = random.choice([0,1,2,3])
        
        return action
    
    def next_state_after_Action(self, action, next_state):
        state = self.curr_state
        Gt = self.R[next_state] + self.gamma*max(self.Q[next_state])
        self.Q[state][action]+=(self.alpha)*(Gt-self.Q[state][action])
        self.curr_state=next_state
        
    def endgame(self):
        
        self.no_of_episodes+=1
        if (self.no_of_episodes<=500):
            pass
        else:
            self.epsilon = 1.0/(1+self.no_of_episodes-500)
            
        self.curr_state=0
        self.totalRewardReceived=0

    def action(self):
        #time.sleep(2)
        action = self.RL_Agent()
        return action

In [2]:
class Environment:
    def __init__(self):
        self.left = chr(129136) #left
        self.up = chr(129137) #up
        self.right = chr(129138) #right
        self.down = chr(129139) #down

        ## symbols to represent possible termination rewards
        self.endWithPositiveRewards = chr(128681) #termination with positive rewards 
        self.endWithNegativeRewards = chr(128163) #termination with negative rewards

        ## symbols to represent player and fish
        self.player = chr(128130) #player
        self.fish = chr(128031) #fish
        
        self.actions = [self.left, self.right, self.up, self.down]
        self.values = [self.player,0,0,0,self.fish,self.endWithNegativeRewards,self.fish,0,self.endWithPositiveRewards]
        
        ## for player
        self.totalRewardReceived = 0
        self.curr_state = 0
        self.e = 0
        

    def display3x3matrix(self):
        print(" ___ ___ ___ ")
        for i in range(3):
            for j in range(3):
                if (isinstance(self.values[3*i+j], int)):
                    print("|",3*i+j,end=" ")
                else:
                    print("|",end="")
                    print(self.values[3*i+j],end=" ")
            print("|")
            print("|___|___|___|")
            
    def newStateAfterAction(self, action):
#         steps_in_that_direction = 1/2.
        steps_in_that_direction=random.choice([1,2])
        self.values[self.curr_state]=0
        if (self.curr_state==0):
            if (action==0): ## left
                self.curr_state=3-steps_in_that_direction
            elif (action==1): ## right
                self.curr_state=steps_in_that_direction
            elif (action==2):## up
                self.curr_state=9-steps_in_that_direction*3
            else: ## down
                self.curr_state=steps_in_that_direction*3
        elif (self.curr_state==1):
            if (action==0): ## left
                self.curr_state=[0,2][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[2,0][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[7,4][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[4,7][steps_in_that_direction-1]
        elif (self.curr_state==2):
            if (action==0): ## left
                self.curr_state=[1,0][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[0,1][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[8,5][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[5,8][steps_in_that_direction-1]
        elif (self.curr_state==3):
            if (action==0): ## left
                self.curr_state=[5,4][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[4,5][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[0,6][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[6,0][steps_in_that_direction-1]   
        elif (self.curr_state==4):
            self.values[4]=self.fish
            if (action==0): ## left
                self.curr_state=[3,5][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[5,3][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[1,7][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[7,1][steps_in_that_direction-1]
        elif (self.curr_state==5):
            if (action==0): ## left
                self.curr_state=[4,3][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[3,4][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[2,8][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[8,2][steps_in_that_direction-1]
        elif (self.curr_state==6):
            self.values[6]=self.fish
            if (action==0): ## left
                self.curr_state=[8,7][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[7,8][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[3,0][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[0,3][steps_in_that_direction-1]
        elif (self.curr_state==7):
            if (action==0): ## left
                self.curr_state=[6,8][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[8,6][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[4,1][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[1,4][steps_in_that_direction-1]
        elif (self.curr_state==8):
            if (action==0): ## left
                self.curr_state=[7,6][steps_in_that_direction-1]
            elif (action==1): ## right
                self.curr_state=[6,7][steps_in_that_direction-1]
            elif (action==2): ## up
                self.curr_state=[5,2][steps_in_that_direction-1]
            else: ## down
                self.curr_state=[2,5][steps_in_that_direction-1]
        if (self.curr_state==5):
            print("Player Died!!")
            self.totalRewardReceived-=10
            self.e=1
        elif (self.curr_state==8):
            print("Player reaches the destination!!")
            self.totalRewardReceived+=10
            self.e=1
        elif (self.curr_state==4 or self.curr_state==6):
            print("Player got a reward of '1' by getting", self.fish)
            self.totalRewardReceived+=1
        else:
            self.totalRewardReceived-=0.1
        self.values[self.curr_state]=self.player
        
    def start_game(self, Player):
        self.totalRewardReceived = 0
        self.e=0 ## Use to determine the end of the game
        self.curr_state=0
        self.display3x3matrix()
        while(not self.e):
            print("Your Current Score", self.totalRewardReceived)
            print("You are currently at", self.curr_state, "position!")
            print("Possible actions to choose:", self.left, self.right, self.up, self.down)
#             time.sleep(2)
            action = Player.action()
            print("You have taken", self.actions[action],"action")
            self.newStateAfterAction(action)
            self.display3x3matrix()
            Player.totalRewardReceived=self.totalRewardReceived
            Player.next_state_after_Action(action, self.curr_state)
        Player.endgame()
        self.values = [self.player,0,0,0,self.fish,self.endWithNegativeRewards,self.fish,0,self.endWithPositiveRewards]
        print("****************************Game Ends!!****************************")
        print("Your Final Score:", self.totalRewardReceived)
        print("****************************Game Ends!!****************************")
        return self.totalRewardReceived

In [3]:
player1=Player()
environment = Environment()

In [4]:
reward = []
for i in range(600):
    totalReward = environment.start_game(player1)
    reward.append(totalReward)

 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡲 action
 ___ ___ ___ 
| 0 | 1 |💂 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.1
You are currently at 2 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡲 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.2
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡱 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 0.8
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡱 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___

| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |💂 |
|___|___|___|
****************************Game Ends!!****************************
Your Final Score: 11
****************************Game Ends!!****************************
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡰 action
 ___ ___ ___ 
| 0 | 1 |💂 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.1
You are currently at 2 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡲 action
 ___ ___ ___ 
| 0 |💂 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.2
You are currently at 1 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 |💂 |🚩 |
|___|___|___|
Your Current Score -0.30000000000000004
You are

| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 1.7999999999999998
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡳 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 1.6999999999999997
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡳 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 1.5999999999999996
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡰 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |💂 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 2.5999999999999996
You are currently at 4 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡲 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 

| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 4.3
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡰 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 |💂 |🚩 |
|___|___|___|
Your Current Score 4.2
You are currently at 7 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |💂 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 5.2
You are currently at 4 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡲 action
Player Died!!
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💂 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
****************************Game Ends!!****************************
Your Final Score: -4.8
****************************Game Ends!!****************************
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|__

|🐟 | 7 |🚩 |
|___|___|___|
****************************Game Ends!!****************************
Your Final Score: -8.5
****************************Game Ends!!****************************
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 0
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.1
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡳 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.2
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡲 action
 ___ ___ ___ 
| 0 |💂 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score -0.30000000000000004
You are currently at 1 position

...

Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 195.90000000000168
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡳 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 195.8000000000017
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 195.7000000000017
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 195.6000000000017
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 

| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 207.40000000000188
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 208.40000000000188
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡳 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 208.3000000000019
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 209.3000000000019
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡳 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|

|___|___|___|
Your Current Score 223.30000000000206
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
explore
You have taken 🡲 action
 ___ ___ ___ 
| 0 | 1 |💂 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 223.20000000000206
You are currently at 2 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡲 action
 ___ ___ ___ 
| 0 |💂 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 223.10000000000207
You are currently at 1 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡳 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |💂 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 224.10000000000207
You are currently at 4 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
 ___ ___ ___ 
| 0 |💂 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Scor

exploit
You have taken 🡳 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 239.10000000000224
You are currently at 0 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 240.10000000000224
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡳 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 240.00000000000225
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 241.00000000000225
You are currently at 6 position!
Possible actions to choose

 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 251.60000000000244
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡳 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 251.50000000000244
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
Player got a reward of '1' by getting 🐟
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
| 3 |🐟 |💣 |
|___|___|___|
|💂 | 7 |🚩 |
|___|___|___|
Your Current Score 252.50000000000244
You are currently at 6 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡳 action
 ___ ___ ___ 
| 0 | 1 | 2 |
|___|___|___|
|💂 |🐟 |💣 |
|___|___|___|
|🐟 | 7 |🚩 |
|___|___|___|
Your Current Score 252.40000000000245
You are currently at 3 position!
Possible actions to choose: 🡰 🡲 🡱 🡳
exploit
You have taken 🡱 action
 ___ ___ ___ 
|💂 | 1 | 2 |
|__

In [5]:
player1.Q

[[30.638686845019844, 40.30325360492396, 154.56411243134497, 95.3060892936358],
 [10.570658610995249,
  10.543152756604849,
  11.394482004927145,
  39.638949737687255],
 [10.284036773802695,
  69.99262761671773,
  2.390273177856571,
  1.2616513384142864],
 [3.933271189460535, 5.37526061069757, 154.67563638899858, 91.26603640482288],
 [-3.2753877337040396,
  -4.249952308952995,
  43.544465223447666,
  9.976857222749196],
 [0, 0, 0, 0],
 [21.200876605002275,
  22.668974360988315,
  59.43966668996788,
  154.31337109683756],
 [10.531691193405791, 96.0505560130768, 9.881618868821844, 10.170971653371385],
 [0, 0, 0, 0]]

In [6]:
max(reward)

252.50000000000227

In [7]:
player1.epsilon

0.009900990099009901